In [9]:
import pandas as pd
import numpy as np

In [ ]:
save_dir = './preprocess'
if not os.path.exists(save_dir):
    os.mkdir(save_dir)

## emotion

In [8]:
import nltk
import re
from nltk.sentiment.vader import SentimentIntensityAnalyzer
# from vaderSentiment.vaderSentiment import SentimentIntensityAnalyzer
import joblib
import pandas as pd
import numpy as np

# ============================== Category ==============================
nvidia_emotions = ['anger', 'anticipation', 'disgust',
                   'fear', 'joy', 'sadness', 'surprise', 'trust']
nvidia_emotions.sort()


def nvidia_arr(emotions_labels_dict=None, emotions_probs_dict=None):
    arr = np.zeros(len(nvidia_emotions)*2)

    if emotions_labels_dict is None or emotions_probs_dict is None:
        return arr

    for i, e in enumerate(nvidia_emotions):
        arr[i] = emotions_labels_dict[e]
        arr[i+len(nvidia_emotions)] = emotions_probs_dict[e]

    return arr

# ============================== Lexicon and Intensity ==============================


# load negation words
negation_words = []
with open('./resources/English/others/negative/negationWords.txt', 'r') as src:
    lines = src.readlines()
    for line in lines:
        negation_words.append(line.strip())

print('\nThe num of negation words: ', len(negation_words))

# load degree words
how_words_dict = dict()
with open('./resources/English/HowNet/intensifierWords.txt', 'r') as src:
    lines = src.readlines()
    for line in lines:
        how_word = line.strip().split()
        how_words_dict[' '.join(how_word[:-1])] = float(how_word[-1])

print('The num of degree words: ', len(how_words_dict),
      '. eg: ', list(how_words_dict.items())[0])


# negation value and degree value
def get_not_and_how_value(cut_words, i, windows):
    not_cnt = 0
    how_v = 1

    left = 0 if (i - windows) < 0 else (i - windows)
    window_text = ' '.join(cut_words[left:i])

    for w in negation_words:
        if w in window_text:
            not_cnt += 1
    for w in how_words_dict.keys():
        if w in window_text:
            how_v *= how_words_dict[w]

    return (-1) ** not_cnt, how_v


lexicon_categories, lexicon_terms2arr = joblib.load(
    './resources/English/NRC/preprocess/preprocess-lexicon.pkl')
print('[NRC Lexicon]\tThere are {} words, including {} categories, every term\'s dimension is {}'.format(
    len(lexicon_terms2arr), len(lexicon_categories), lexicon_terms2arr['happy'].shape))

intensity_categories, intensity_terms2arr = joblib.load(
    './resources/English/NRC/preprocess/preprocess-intensity.pkl')
print('[NRC Intensity]\tThere are {} words, including {} categories, every term\'s dimension is {}'.format(
    len(intensity_terms2arr), len(intensity_categories), intensity_terms2arr['happy'].shape))

nrc_emotion_words = set(lexicon_terms2arr.keys()).union(
    set(intensity_terms2arr.keys()))


def nrc_arr(cut_words, windows=4):
    arr = np.zeros(len(lexicon_categories) + len(intensity_categories))

    for i, word in enumerate(cut_words):
        if word in nrc_emotion_words:
            not_v, how_v = get_not_and_how_value(cut_words, i, windows)

            if word in lexicon_terms2arr:
                arr[:len(lexicon_categories)] += not_v * \
                    how_v * lexicon_terms2arr[word]
            if word in intensity_terms2arr:
                arr[len(lexicon_categories):] += not_v * \
                    how_v * intensity_terms2arr[word]

    return arr

# ============================== Sentiment Scores ==============================


sentiment_analyzer = SentimentIntensityAnalyzer()


def sentiment_score(text):
    scores = sentiment_analyzer.polarity_scores(text)
    return scores['pos'], scores['neg'], scores['neu'], scores['compound']

# ============================== Auxilary Features ==============================


# Emoticon
def isEmoji(content):
    if not content:
        return False
    if u"\U0001F600" <= content and content <= u"\U0001F64F":
        return True
    elif u"\U0001F300" <= content and content <= u"\U0001F5FF":
        return True
    elif u"\U0001F680" <= content and content <= u"\U0001F6FF":
        return True
    elif u"\U0001F1E0" <= content and content <= u"\U0001F1FF":
        return True
    else:
        return False


def emoji_count(text):
    emoji = 0
    for c in text:
        if isEmoji(c):
            emoji += 1
    return emoji / len(text)


smiling_emoticons = [':-)', ':)', ':o)', ':],' ':3',
                     ':c)', ':>' '=]', '8)', '=)', ':}', ':^)', ':っ)']
frowning_emoticons = [
    '>:[', ':-(', ':(', ':-c', ':c', ':-<', ':っC', ':<', ':-[', ':[', ':{']


def emoticon_arr(text):
    smiling = 0
    frowning = 0
    for s in smiling_emoticons:
        smiling += text.count(s)
    for f in frowning_emoticons:
        frowning += text.count(f)
    return smiling / len(text), frowning / len(text), emoji_count(text)


# Punctuation
def symbols_count(text):
    excl = (text.count('!') + text.count('！')) / len(text)
    ques = (text.count('?') + text.count('？')) / len(text)
    comma = (text.count(',') + text.count('，')) / len(text)
    dot = (text.count('.') + text.count('。')) / len(text)
    ellip = (text.count('..') + text.count('。。')) / len(text)

    return excl, ques, comma, dot, ellip


# Sentimental Words
def init_words(file):
    with open(file, 'r', encoding='utf-8') as src:
        words = src.readlines()
        words = [l.strip() for l in words]
    print('File: {}, Words_sz = {}'.format(file.split('/')[-1], len(words)))
    return list(set(words))


print()
pos_words = init_words('./resources/English/HowNet/正面情感词语（英文）.txt')
pos_words += init_words('./resources/English/HowNet/正面评价词语（英文）.txt')
neg_words = init_words('./resources/English/HowNet/负面情感词语（英文）.txt')
neg_words += init_words('./resources/English/HowNet/负面评价词语（英文）.txt')

pos_words = set(pos_words)
neg_words = set(neg_words)
print('[HowNet]\tThere are {} positive words and {} negative words'.format(
    len(pos_words), len(neg_words)))


def sentiment_words_count(cut_words):
    if len(cut_words) == 0:
        return [0, 0, 0, 0]

    # positive and negative words
    sentiment = []
    for words in [pos_words, neg_words]:
        c = 0
        for word in words:
            if word in cut_words:
                # print(word)
                c += 1
        sentiment.append(c)
    sentiment = [c / len(cut_words) for c in sentiment]

    # degree words
    degree = 0
    for word in how_words_dict:
        if word in cut_words:
            # print(word)
            degree += how_words_dict[word]

    # negation words
    negation = 0
    for word in negation_words:
        negation += cut_words.count(word)
    negation /= len(cut_words)

    sentiment += [degree, negation]

    return sentiment


# Personal Pronoun
first_pronoun = init_words(
    './resources/English/others/pronoun/1-personal-pronoun.txt')
second_pronoun = init_words(
    './resources/English/others/pronoun/2-personal-pronoun.txt')
third_pronoun = init_words(
    './resources/English/others/pronoun/3-personal-pronoun.txt')
pronoun_words = [first_pronoun, second_pronoun, third_pronoun]


def pronoun_count(cut_words):
    if len(cut_words) == 0:
        return [0, 0, 0]

    pronoun = []
    for words in pronoun_words:
        c = 0
        for word in words:
            c += cut_words.count(word)
        pronoun.append(c)

    return [c / len(cut_words) for c in pronoun]

# others


def upper_letter_count(text):
    upper = 0
    for c in text:
        if c.isupper():
            upper += 1
    return upper / len(text)


# Auxilary Features
def auxilary_features(text, cut_words):
    arr = np.zeros(16)

    arr[:3] = emoticon_arr(text)
    arr[3:8] = symbols_count(text)
    arr[8:12] = sentiment_words_count(cut_words)
    arr[12:15] = pronoun_count(cut_words)
    arr[15:16] = upper_letter_count(text)

    return arr


# ============================== Main ==============================


def del_url_at(text):
    pattern = re.compile(
        'http[s]?://(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    urls = re.findall(pattern, text)
    for url in urls:
        text = text.replace(url, '')

    pattern = re.compile(
        '@(?:[a-zA-Z]|[0-9]|[$-_@.&+]|[!*\(\),]|(?:%[0-9a-fA-F][0-9a-fA-F]))+')
    ats = re.findall(pattern, text)
    for at in ats:
        text = text.replace(at, '')

    text = text.replace('', '').replace('\r', '').replace('\t', '')
    return text


def cut_words_from_text(text):
    pattern = r"""(?x)                   # set flag to allow verbose regexps 
                  (?:[A-Z]\.)+           # abbreviations, e.g. U.S.A. 
                  |\d+(?:\.\d+)?%?       # numbers, incl. currency and percentages 
                  |\w+(?:[-']\w+)*       # words w/ optional internal hyphens/apostrophe 
                  |\.\.\.                # ellipsis 
                  |(?:[.,;"'?():-_`!])    # special characters with meanings 
                """

    return nltk.regexp_tokenize(del_url_at(text), pattern)


def extract_publisher_emotion(content, content_words, emotions_labels_dict=None, emotions_probs_dict=None):
    text, cut_words = content, content_words

    arr = np.zeros(54)

    arr[:16] = np.zeros(16)
    #arr[:16] = nvidia_arr(emotions_labels_dict, emotions_probs_dict)
    arr[16:34] = nrc_arr(cut_words)
    arr[34:38] = sentiment_score(text)
    arr[38:54] = auxilary_features(text, cut_words)

    return arr


def extract_social_emotion(comments, comments_words, mean_emotions_labels_dict, max_emotions_labels_dict, mean_emotions_probs_dict, max_emotions_probs_dict):
    if len(comments) == 0:
        arr = np.zeros(54)
        mean_arr, max_arr = arr, arr
        return mean_arr, max_arr, np.concatenate([mean_arr, max_arr])

    arr = np.zeros((len(comments), 54))

    for i in range(len(comments)):
        arr[i] = extract_publisher_emotion(
            comments[i], comments_words[i], None, None)

    mean_arr = np.mean(arr, axis=0)
    max_arr = np.max(arr, axis=0)

    mean_arr[:16] = nvidia_arr(
        mean_emotions_labels_dict, mean_emotions_probs_dict)
    max_arr[:16] = nvidia_arr(
        max_emotions_labels_dict, max_emotions_probs_dict)

    return mean_arr, max_arr, np.concatenate([mean_arr, max_arr])


def extract_dual_emotion(piece, COMMENTS=100):
    for k in ['content_emotions_labels', 'content_emotions_probs', 'comments100_emotions_labels_mean_pooling', 'comments100_emotions_labels_max_pooling', 'comments100_emotions_probs_mean_pooling', 'comments100_emotions_probs_max_pooling']:
        if k not in piece:
            piece[k] = None

    publisher_emotion = extract_publisher_emotion(
        piece['content'], piece['content_words'], piece['content_emotions_labels'], piece['content_emotions_probs'])
    mean_arr, max_arr, social_emotion = extract_social_emotion(
        piece['comments'][:COMMENTS], piece['comments_words'][:COMMENTS], piece['comments100_emotions_labels_mean_pooling'], piece['comments100_emotions_labels_max_pooling'], piece['comments100_emotions_probs_mean_pooling'], piece['comments100_emotions_probs_max_pooling'])
    emotion_gap = np.concatenate(
        [publisher_emotion - mean_arr, publisher_emotion - max_arr])

    dual_emotion = np.concatenate(
        [publisher_emotion, social_emotion, emotion_gap])
    return dual_emotion



The num of negation words:  26
The num of degree words:  157 . eg:  ('100 percent', 2.0)
[NRC Lexicon]	There are 14182 words, including 10 categories, every term's dimension is (10,)
[NRC Intensity]	There are 5975 words, including 8 categories, every term's dimension is (8,)

File: 正面情感词语（英文）.txt, Words_sz = 769
File: 正面评价词语（英文）.txt, Words_sz = 3594
File: 负面情感词语（英文）.txt, Words_sz = 1011
File: 负面评价词语（英文）.txt, Words_sz = 3563
[HowNet]	There are 4349 positive words and 4534 negative words
File: 1-personal-pronoun.txt, Words_sz = 8
File: 2-personal-pronoun.txt, Words_sz = 3
File: 3-personal-pronoun.txt, Words_sz = 12


### gossipcop

In [11]:
path1 = './rawdata/gossipcop.csv'

gossipcop = pd.read_csv(path1)
gossipcop.head(5)

news_id  label                                            content
0  gossipcop-879076      0  She has no problem packing her concerts with t...
1  gossipcop-867833      0  The BBC has responded to complaints made again...
2  gossipcop-874403      0  Somali model, actress, and entrepreneur  Iman ...
3  gossipcop-896234      0  Story highlights Rance Howard was cast in many...
4  gossipcop-878670      0  Sam Smith is single—like really single.  Durin...

In [12]:
gossipcop.shape

(16599, 3)

In [13]:
gossipcop["label"].value_counts()

label
0    12641
1     3958
Name: count, dtype: int64

In [40]:
gossipcop['content_words']=''
for i in range(len(gossipcop)): 
    gossipcop['content_words'][i] = cut_words_from_text(gossipcop['content'][i])

<ipython-input-40-5625edae24c7>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gossipcop['content_words'][i] = cut_words_from_text(gossipcop['content'][i])
<ipython-input-40-5625edae24c7>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gossipcop['content_words'][i] = cut_words_from_text(gossipcop['content'][i])
<ipython-input-40-5625edae24c7>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  gossipcop['content_words'][i] = cut_words_

In [16]:
nvidia_arr(emotions_labels_dict, emotions_probs_dict)

NameError: name 'emotions_labels_dict' is not defined

In [41]:
nrc_arr(gossipcop['content_words'][0])

array([ 1.    , 12.    ,  2.    ,  4.    , 14.    , 12.5   , 54.    ,
       14.    ,  2.    , 20.5   ,  1.723 ,  6.702 ,  1.031 ,  2.748 ,
       11.3975,  5.649 ,  6.203 , 11.561 ])

In [15]:
sentiment_score(gossipcop["content"][0])

(0.148, 0.02, 0.831, 0.9995)

In [21]:
auxilary_features(gossipcop['content'][0],gossipcop['content_words'][0])

array([0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 1.18203310e-03,
       1.47754137e-04, 6.05791962e-03, 3.10283688e-03, 1.47754137e-04,
       2.43111831e-02, 1.37763371e-02, 1.50000000e+01, 2.43111831e-03,
       2.43111831e-03, 0.00000000e+00, 5.26742301e-02, 2.86643026e-02])

In [63]:
emotion_arr = [extract_publisher_emotion(gossipcop['content'][i], gossipcop['content_words'][i],None,None) for i in range(len(gossipcop))]
emotion_arr = np.array(emotion_arr)
emotion_arr

[array([0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        1.00000000e+00, 1.20000000e+01, 2.00000000e+00, 4.00000000e+00,
        1.40000000e+01, 1.25000000e+01, 5.40000000e+01, 1.40000000e+01,
        2.00000000e+00, 2.05000000e+01, 1.72300000e+00, 6.70200000e+00,
        1.03100000e+00, 2.74800000e+00, 1.13975000e+01, 5.64900000e+00,
        6.20300000e+00, 1.15610000e+01, 1.48000000e-01, 2.00000000e-02,
        8.31000000e-01, 9.99500000e-01, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 1.18203310e-03, 1.47754137e-04, 6.05791962e-03,
        3.10283688e-03, 1.47754137e-04, 2.43111831e-02, 1.37763371e-02,
        1.50000000e+01, 2.43111831e-03, 2.43111831e-03, 0.00000000e+00,
        5.26742301e-02, 2.86643026e-02]),
 array([0.00000000e+00

In [64]:
emotion_arr.shape

(16599, 54)

In [65]:
np.save(os.path.join(save_dir, 'emotion_arr_gossipcop.npy'), emotion_arr)

### politifact

In [46]:
path2 = './rawdata/politifact.csv'

politifact = pd.read_csv(path2)
politifact.head(5)

news_id  label                                            content
0  politifact12773      0  President Bush went to a Muslim community cent...
1    politifact495      0  This is part one of the transcript for the CNN...
2  politifact14474      0  Amendment XXV  Section 1.  In case of the remo...
3    politifact567      0  For Immediate Release  July 9, 2008 Contact: P...
4  politifact12052      0  TRUMP: Well, if Ted was listening, he would ha...

In [47]:
politifact.shape

(497, 3)

In [48]:
politifact["label"].value_counts()

label
1    272
0    225
Name: count, dtype: int64

In [49]:
politifact['content_words']=''
for i in range(len(politifact)): 
    politifact['content_words'][i] = cut_words_from_text(politifact['content'][i])

<ipython-input-49-faeaa518c97e>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  politifact['content_words'][i] = cut_words_from_text(politifact['content'][i])
<ipython-input-49-faeaa518c97e>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  politifact['content_words'][i] = cut_words_from_text(politifact['content'][i])
<ipython-input-49-faeaa518c97e>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  politifact['content_words'][i] = cut_w

In [66]:
emotion_arr = [extract_publisher_emotion(politifact['content'][i], politifact['content_words'][i],None,None) for i in range(len(politifact))]
emotion_arr = np.array(emotion_arr)
emotion_arr

array([[0.        , 0.        , 0.        , ..., 0.        , 0.01459854,
        0.02034429],
       [0.        , 0.        , 0.        , ..., 0.01068947, 0.01722193,
        0.06363094],
       [0.        , 0.        , 0.        , ..., 0.        , 0.03512881,
        0.03101737],
       ...,
       [0.        , 0.        , 0.        , ..., 0.        , 0.02347418,
        0.02491924],
       [0.        , 0.        , 0.        , ..., 0.        , 0.0247678 ,
        0.05222222],
       [0.        , 0.        , 0.        , ..., 0.        , 0.00826446,
        0.03475513]])

In [67]:
emotion_arr.shape

(497, 54)

In [68]:
np.save(os.path.join(save_dir, 'emotion_arr_politifact.npy'), emotion_arr)

## semantics

### gossipcop

In [44]:
import numpy as np
import json
import time
import os
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import sys
sys.path.append('./word-embedding')
from load_embeddings import load_embeddings

MAX_NUM_WORDS = 6000

embeddings_index = load_embeddings(
    language='English', embeddings_file='./word-embedding/glove.twitter.27B.200d.txt')
CONTENT_WORDS = 50
EMBEDDING_DIM = 200


texts=[]
for i in range(len(gossipcop)):
    texts += [gossipcop['content_words'][i]]

tokenizer = Tokenizer(num_words=MAX_NUM_WORDS)
tokenizer.fit_on_texts(texts)
sequences = tokenizer.texts_to_sequences(texts)
word_index = tokenizer.word_index
print('Found {} unique tokens.'.format(len(word_index)))

content_arr = pad_sequences(sequences, maxlen=CONTENT_WORDS)
print('Content Array: {}'.format(content_arr.shape))

np.save(os.path.join(save_dir, 'content_arr_gossipcop.npy'), content_arr)

num_words = min(MAX_NUM_WORDS, len(word_index) + 1)
embedding_matrix = np.random.randn(num_words, EMBEDDING_DIM)
for word, i in word_index.items():
    if i >= MAX_NUM_WORDS:
        continue
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        embedding_matrix[i] = embedding_vector
print('Embedding Matrix: {}'.format(embedding_matrix.shape))

np.save(os.path.join(save_dir, 'embedding_matrix_{}_gossipcop.npy'.format(embedding_matrix.shape)), embedding_matrix)


File: ./word-embedding/glove.twitter.27B.200d.txt, there are 1193515 vectors
Found 127388 unique tokens.
Content Array: (16599, 50)
Embedding Matrix: (6000, 200)


### politifact

In [50]:
import numpy as np
import json
import time
import os
from keras.preprocessing.text import Tokenizer
from keras.preprocessing.sequence import pad_sequences
import sys
sys.path.append('./word-embedding')
from load_embeddings import load_embeddings

save_dir = './preprocess'
if not os.path.exists(save_dir):
    os.mkdir(save_dir)


MAX_NUM_WORDS = 6000

embeddings_index = load_embeddings(
    language='English', embeddings_file='./word-embedding/glove.twitter.27B.200d.txt')
CONTENT_WORDS = 50
EMBEDDING_DIM = 200


texts=[]
for i in range(len(politifact)):
    texts += [politifact['content_words'][i]]

tokenizer = Tokenizer(num_words=MAX_NUM_WORDS)
tokenizer.fit_on_texts(texts)
sequences = tokenizer.texts_to_sequences(texts)
word_index = tokenizer.word_index
print('Found {} unique tokens.'.format(len(word_index)))

content_arr = pad_sequences(sequences, maxlen=CONTENT_WORDS)
print('Content Array: {}'.format(content_arr.shape))

np.save(os.path.join(save_dir, 'content_arr_politifact.npy'), content_arr)

num_words = min(MAX_NUM_WORDS, len(word_index) + 1)
embedding_matrix = np.random.randn(num_words, EMBEDDING_DIM)
for word, i in word_index.items():
    if i >= MAX_NUM_WORDS:
        continue
    embedding_vector = embeddings_index.get(word)
    if embedding_vector is not None:
        embedding_matrix[i] = embedding_vector
print('Embedding Matrix: {}'.format(embedding_matrix.shape))

np.save(os.path.join(save_dir, 'embedding_matrix_{}_politifact.npy'.format(embedding_matrix.shape)), embedding_matrix)


File: ./word-embedding/glove.twitter.27B.200d.txt, there are 1193515 vectors
Found 24825 unique tokens.
Content Array: (497, 50)
Embedding Matrix: (6000, 200)
